In [1]:
import mlflow
import pandas as pd

from sklearn.preprocessing import MinMaxScaler, OneHotEncoder
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC
from sklearn import metrics

import imblearn
from collections import Counter
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from imblearn.pipeline import Pipeline

In [2]:
import pickle

In [3]:
from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from hyperopt.pyll import scope
import numpy as np

In [4]:
import xgboost as xgb

In [5]:
import lightgbm as lgb
import warnings
import logging

In [6]:
import os

In [7]:
os.environ[
    "GOOGLE_APPLICATION_CREDENTIALS"] = "secret.json"

In [8]:
mlflow.autolog(silent=True)

In [9]:
warnings.filterwarnings('ignore')

### Load dataframe

In [6]:
df = pd.read_csv("data/telco-customers.csv")

In [8]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7043 entries, 0 to 7042
Data columns (total 21 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   customerID        7043 non-null   object 
 1   gender            7043 non-null   object 
 2   SeniorCitizen     7043 non-null   int64  
 3   Partner           7043 non-null   object 
 4   Dependents        7043 non-null   object 
 5   tenure            7043 non-null   int64  
 6   PhoneService      7043 non-null   object 
 7   MultipleLines     7043 non-null   object 
 8   InternetService   7043 non-null   object 
 9   OnlineSecurity    7043 non-null   object 
 10  OnlineBackup      7043 non-null   object 
 11  DeviceProtection  7043 non-null   object 
 12  TechSupport       7043 non-null   object 
 13  StreamingTV       7043 non-null   object 
 14  StreamingMovies   7043 non-null   object 
 15  Contract          7043 non-null   object 
 16  PaperlessBilling  7043 non-null   object 


In [15]:
df.gender.unique()

array(['Female', 'Male'], dtype=object)

In [11]:
train = df.sample(frac=0.8, random_state=42)
test = df.drop(train.index)

In [12]:
train.to_csv("data/train.csv", index=False)
test.to_csv("data/test.csv", index=False)

In [13]:
train.groupby("Churn").size()

Churn
No     4122
Yes    1512
dtype: int64

In [14]:
test.groupby("Churn").size()

Churn
No     1052
Yes     357
dtype: int64

In [15]:
ohe = OneHotEncoder(sparse=False)

In [16]:
num_features = ["tenure", "MonthlyCharges", "TotalCharges"]

cat_features = [
     'gender',
     'SeniorCitizen',
     'Partner',
     'Dependents',
     'PhoneService',
     'MultipleLines',
     'InternetService',
     'OnlineSecurity',
     'OnlineBackup',
     'DeviceProtection',
     'TechSupport',
     'StreamingTV',
     'StreamingMovies',
     'Contract',
     'PaperlessBilling',
     'PaymentMethod'
               ]

In [17]:
def prepare_dataset(df):
    df.TotalCharges = pd.to_numeric(df.TotalCharges, errors='coerce')
    df = df.iloc[:,1:]
    df = df.dropna()
    df = df.reset_index(drop=True)

    df['Churn'] = df['Churn'].replace(to_replace='Yes', value=1)
    df['Churn'] = df['Churn'].replace(to_replace='No',  value=0)

    df_dummies = ohe.fit_transform(df[cat_features])
    X = pd.DataFrame(df_dummies, columns=ohe.get_feature_names_out())
    X = pd.concat([X, df[num_features]], axis=1)
    y = df['Churn'].values

    features = X.columns.values
    scaler = MinMaxScaler(feature_range = (0,1))
    
    X = pd.DataFrame(scaler.fit_transform(X))
    X.columns = features
    
    with open('app/models/min_max_scaler.bin', 'wb') as f_out:
        pickle.dump(scaler, f_out)
        
    with open('app/models/ohe.bin', 'wb') as f_out:
        pickle.dump(ohe, f_out)
    
    return X, y

In [18]:
X, y = prepare_dataset(train)

In [19]:
over = SMOTE(sampling_strategy = 1)

X, y = over.fit_resample(X, y)
Counter(y)

Counter({1: 4115, 0: 4115})

In [20]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=101, shuffle=True)

### Training models

In [21]:
TRACKING_SERVER_HOST = "34.88.78.177"
# mlflow.set_tracking_uri("app/sqlite:///mlflow.db")

mlflow.set_tracking_uri(f"http://{TRACKING_SERVER_HOST}:5000")
mlflow.set_experiment("telco-customers-churn")

mlflow.sklearn.autolog()

In [22]:
# experiment = mlflow.get_experiment_by_name("telco-customers-churn")
# runs = mlflow.search_runs(experiment.experiment_id)

# # Delete all the runs.
# for run in runs.run_id:
#     mlflow.delete_run(run)

In [23]:
def train_with_mlflow(model,  model_name):
    with mlflow.start_run():
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)
        recall = metrics.recall_score(y_test, y_pred)
        f1 = metrics.f1_score(y_test, y_pred)
        accuracy = metrics.accuracy_score(y_test, y_pred)
        roc = metrics.roc_auc_score(y_test, y_pred)
        
        mlflow.log_metrics(
            {
                "test_recall_score": recall,
                "test_f1_score": f1,
                "test_accuracy_score": accuracy,
                "test_roc_auc_score": roc
            }
        )
        
        mlflow.log_param("model", model_name)

In [24]:
lr = LogisticRegression()
train_with_mlflow(lr, "logistic regression")

In [25]:
svc = SVC(kernel='linear') 
train_with_mlflow(svc, "SVC")

In [26]:
ada = AdaBoostClassifier()
train_with_mlflow(ada, "AdaBoostClassifier")

In [27]:
space = {
    'n_estimators': hp.choice('n_estimators', np.arange(50, 200, dtype=int)),
    'max_depth': hp.choice('max_depth', np.arange(1, 20, dtype=int)),
    'min_samples_split': hp.uniform('min_samples_split', 0.1, 1.0),
    'min_samples_leaf': hp.uniform('min_samples_leaf', 0.1, 0.5),
}

def objective(params):
    with mlflow.start_run():
        clf = RandomForestClassifier(**params, random_state=42)
        clf.fit(X_train, y_train)
        y_pred = clf.predict(X_test)
        recall = metrics.recall_score(y_test, y_pred)
        f1 = metrics.f1_score(y_test, y_pred)
        accuracy = metrics.accuracy_score(y_test, y_pred)
        roc = metrics.roc_auc_score(y_test, y_pred)
        
        mlflow.log_metrics(
            {
                "test_recall_score": recall,
                "test_f1_score": f1,
                "test_accuracy_score": accuracy,
                "test_roc_auc_score": roc
            }
        )
        mlflow.log_param("model", "random_forest")
        return recall
    
best = fmin(fn=objective, space=space, algo=tpe.suggest, max_evals=50, verbose=1, trials=Trials())

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [04:04<00:00,  4.89s/trial, best loss: 0.0]


In [28]:
mlflow.xgboost.autolog()

In [29]:
space = {
    'n_estimators': hp.choice('n_estimators', np.arange(50, 200, dtype=int)),
    'max_depth': hp.choice('max_depth', np.arange(1, 20, dtype=int)),
    'learning_rate': hp.uniform('learning_rate', 0.001, 0.3),
    'min_child_weight': hp.uniform('min_child_weight', 1, 10),
    'subsample': hp.uniform('subsample', 0.5, 1),
    'gamma': hp.uniform('gamma', 0, 1),
    'colsample_bytree': hp.uniform('colsample_bytree', 0.5, 1),
}

def objective(params):
    with mlflow.start_run():
        clf = xgb.XGBClassifier(**params, random_state=42)
        clf.fit(X_train, y_train)
        y_pred = clf.predict(X_test)
        recall = metrics.recall_score(y_test, y_pred)
        f1 = metrics.f1_score(y_test, y_pred)
        accuracy = metrics.accuracy_score(y_test, y_pred)
        roc = metrics.roc_auc_score(y_test, y_pred)
        
        mlflow.log_metrics(
            {
                "test_recall_score": recall,
                "test_f1_score": f1,
                "test_accuracy_score": accuracy,
                "test_roc_auc_score": roc
            }
        )
        
        mlflow.log_param("model", "xgboost")
        return recall

In [ ]:
best = fmin(fn=objective, space=space, algo=tpe.suggest, max_evals=500, verbose=1, trials=Trials())

  3%|███▌                                                                                                                                       | 13/500 [01:29<55:43,  6.86s/trial, best loss: 0.8428686543110395]


KeyboardInterrupt: 

In [31]:
mlflow.lightgbm.autolog()

In [32]:
logging.getLogger('lightgbm').setLevel(logging.ERROR)

In [33]:
space = {
    'n_estimators': hp.choice('n_estimators', np.arange(50, 200, dtype=int)),
    'max_depth': hp.choice('max_depth', np.arange(1, 20, dtype=int)),
    'learning_rate': hp.uniform('learning_rate', 0.001, 0.3),
    'min_child_weight': hp.uniform('min_child_weight', 1, 10),
    'num_leaves': hp.choice('num_leaves', np.arange(2, 100, dtype=int)),
    'subsample': hp.uniform('subsample', 0.5, 1),
    'colsample_bytree': hp.uniform('colsample_bytree', 0.5, 1),
}

def objective(params):
    with mlflow.start_run():
        clf = lgb.LGBMClassifier(**params, random_state=42)
        clf.fit(X_train, y_train)
        y_pred = clf.predict(X_test)
        recall = metrics.recall_score(y_test, y_pred)
        f1 = metrics.f1_score(y_test, y_pred)
        accuracy = metrics.accuracy_score(y_test, y_pred)
        roc = metrics.roc_auc_score(y_test, y_pred)
        
        mlflow.log_metrics(
            {
                "test_recall_score": recall,
                "test_f1_score": f1,
                "test_accuracy_score": accuracy,
                "test_roc_auc_score": roc
            }
        )
        
        mlflow.log_param("model", "lightgbm")
        return recall

# Assuming you have X_train, X_test, y_train, and y_test datasets available

# Trials object to track the results
trials = Trials()

# Run the hyperparameter search using TPE (Tree-structured Parzen Estimator) algorithm
best = fmin(fn=objective,
            space=space,
            algo=tpe.suggest,
            max_evals=500,  # Number of iterations for hyperparameter search
            trials=trials,
            verbose=1) 

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines                                                                                                                                    
[LightGBM] [Info] Number of positive: 2874, number of negative: 2887                                                                                                                                               
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002976 seconds.                                                                                                         
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2509                                                                                                                                                                                  
[LightGBM] [Info] Number of da

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

[LightGBM] [Info] Start training from score -0.004513                                                                                                                                                              
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                                                                                         
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf                                                                              

In [ ]:
best